# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. 

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [1]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [2]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run

In [3]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * cov

def optional_mean_func(gp_obj,x,hyperparameters):
    return ((x[:,0] ** 2 + x[:,1] - 11.0) ** 2 + (x[:,0] + x[:,1] ** 2 - 7.0) ** 2) * hyperparameters[-1]

def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n
def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just need a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this funciton is not needed
    from scipy.optimize import differential_evolution as devo
    print("Cost adjustment in progress...")
    print("old cost parameters: ",parameters)
    bounds = np.array([[0.001,10],[0.0001,10]])
    ###remove outliers:
    origins = []
    points = []
    motions = []
    c   = []
    cost_per_motion = []
    for i in range(len(costs)):
        origins.append(costs[i][0])
        points.append(costs[i][1])
        motions.append(abs(costs[i][0] - costs[i][1]))
        c.append(costs[i][2])
        cost_per_motion.append(costs[i][2]/optional_cost_function(costs[i][0],costs[i][1], parameters))
    mean_costs_per_distance = np.mean(np.asarray(cost_per_motion))
    sd = np.std(np.asarray(cost_per_motion))
    for element in cost_per_motion:
        if (
            element >= mean_costs_per_distance - 2.0 * sd
            and element <= mean_costs_per_distance + 2.0 * sd
        ):
            continue
        else:
            motions.pop(cost_per_motion.index(element))
            c.pop(cost_per_motion.index(element))
            origins.pop(cost_per_motion.index(element))
            points.pop(cost_per_motion.index(element))
            cost_per_motion.pop(cost_per_motion.index(element))
    def compute_l1_cost_misfit(params, origins,points, costs):
        parameters = {"offset": params[0], "slope": params[1]}
        sum1 = 0.0
        for idx in range(len(points)):
            sum1 = sum1 + (
                (optional_cost_function(origins[idx],points[idx],parameters) - costs[idx]) ** 2)
        return sum1
    res = devo(compute_l1_cost_misfit, bounds, args = (origins, points,c), tol=1e-6, disp=True, maxiter=300, popsize=20,polish=False)
    arguments = {"offset": res["x"][0],"slope": res["x"][1:]}
    print("New cost parameters: ", arguments)
    return arguments

In [4]:
import time
from gpcam.autonomous_experimenter import AutonomousExperimenterGP

def instrument(data):
    for entry in data:
        entry["value"] = np.sin(np.linalg.norm(entry["position"]))
        #entry["cost"]  = [np.array([0,0]),entry["position"],np.sum(entry["position"])]
    return data
#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),instrument,
                                 np.ones((3)),np.array([[0.001,100],[0.001,100],[0.001,100]]),
                                 init_dataset_size= 20, 
                                 acq_func = "covariance", #optional_acq_func, 
                                 #cost_func = optional_cost_function, 
                                 #cost_update_func = optional_cost_update_function,
                                 cost_func_params={"offset": 5.0,"slope":10.0},
                                 kernel_func = None)#, prior_mean_func = optional_mean_func)


print("length of the dataset: ",len(my_ae.x))

#training
import time
start_time = time.time()
my_ae.train_async(max_iter = 2) #train asynchronously
my_ae.opt_obj.get_final()
end_time = time.time()
print(end_time - start_time)
#my_ae.train()       #or not
#print("Initial training submitted")
#for i in range(2): #this loop shows how hyperparameters are changing if they are trained asynchronously
#    time.sleep(2)
#     my_ae.update_hps()
#my_ae.train_async()
#my_ae.update_hps()

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
Costs successfully initialized
##################################################################################
Initialization successfully concluded
now train(...) or train_async(...), and then go(...)
##################################################################################
length of the dataset:  20
Async fvGP training started with  20  data points
fvGP submitted HGDL optimization for asynchronous training
bounds: [[1.e-03 1.e+02]
 [1.e-03 1.e+02]
 [1.e-03 1.e+02]]
deflation radius:  None
HGDL successfully initiated
deflation radius set to  0.09999899999999999
Host  tcp://127.0.0.1:33879  has  3  workers.
<Client: 'tcp://127.0.0.1:46299' processes=4 threads=16, memory=31.30 GiB>
HGDL starts with:  [[ 1.          1.          1.        ]
 [98.56694223 48.79748736 64.0558805 ]
 [45.26165764 10.31271388 81.09485293

In [5]:
my_ae.kill_client()

fvGP is killing asynchronous training....
HGDL kill client initialized ...
HGDL kill client successful
fvGP successfully killed the training.


## Let's see what our initial model looks like

In [6]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x,my_ae.y]))

## Let's run the autonomus loop to 100 points

In [7]:
help(my_ae.go)

Help on method go in module gpcam.autonomous_experimenter:

go(N=1000000000000000.0, breaking_error=1e-50, retrain_globally_at=[100, 400, 1000], retrain_locally_at=[20, 40, 60, 80, 100, 200, 400, 1000], retrain_async_at=[1000, 2000, 5000, 10000], retrain_callable_at=[], update_cost_func_at=[], acq_func_opt_setting=<function AutonomousExperimenterGP.<lambda> at 0x7f64fb17da60>, training_opt_callable=None, training_opt_max_iter=20, training_opt_pop_size=10, training_opt_tol=1e-06, acq_func_opt_max_iter=20, acq_func_opt_pop_size=20, acq_func_opt_tol=1e-06, acq_func_opt_tol_adjust=[True, 0.1], number_of_suggested_measurements=1) method of gpcam.autonomous_experimenter.AutonomousExperimenterGP instance
    function to start the autonomous-data-acquisition loop
    optional parameters:
    -----------
        * N = 1e15 ... run N iterations
        * breaking_error = 1e-15 ... run until breaking_error is achieved
        * retrain_globally_at = [100,400,1000]
        * retrain_locally_at = [

In [8]:
#run the loop
my_ae.go(N = 100, 
            retrain_async_at=[],
            retrain_globally_at = [],
            retrain_locally_at = [],
            acq_func_opt_setting = lambda number: "global" if number % 2 == 0 else "local",
            training_opt_callable = None,
            training_opt_max_iter = 20,
            training_opt_pop_size = 10,
            training_opt_tol      = 1e-6,
            acq_func_opt_max_iter = 20,
            acq_func_opt_pop_size = 20,
            acq_func_opt_tol      = 1e-6,
            acq_func_opt_tol_adjust = [True,0.1])#,update_cost_func_at = [30])
print("length of the dataset is now: ", len(my_ae.x))
#and that runs the autonomous loop

Date and time:        2021-07-28_16_42_48



iteration:  20
Run Time:  0.0003604888916015625      seconds
Number of measurements:  20
hps:  [1. 1. 1.]
ask() initiated with hyperparameters: [1. 1. 1.]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  1e-06
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -0.99282
differential_evolution step 2: f(x)= -0.997305
differential_evolution step 3: f(x)= -0.997749
differential_evolution step 4: f(x)= -0.997749
differential_evolution step 5: f(x)= -0.998047
differential_evolution step 6: f(x)= -0.998842
differential_evolution step 7: f(x)= -0.998842
differential_evolution step 8: f(x)= -0.999122
differential_evolution step 9: f(x)= -0.999122
differential_evolution step 10: f(x)= -0.999122
differential_evolution step 11: f(x)= -0.999122
differential_

differential_evolution step 3: f(x)= -0.499938
The acquisition function optimization resulted in: 
     x:  [[9.87681277 4.06576503]]
  f(x):  [-0.49993793]
acquisition funciton optimization tolerance changed to:  0.04999379291027281
Next points to be requested: 
[[9.87681277 4.06576503]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.27357523 1.37891145 1.09493401]
The GPOptimizer updated the Hyperperameters:  [0.27357523 1.37891145 1.09493401]
The Autonomus Experimenter updated the hyperparameters
hps:  [0.27357523

differential_evolution step 3: f(x)= -0.484734
differential_evolution step 4: f(x)= -0.484734
The acquisition function optimization resulted in: 
     x:  [[9.2592899  9.82684169]]
  f(x):  [-0.4847343]
acquisition funciton optimization tolerance changed to:  0.048473429551275614
Next points to be requested: 
[[9.2592899  9.82684169]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.27357523 1.37891145 1.09493401]
The GPOptimizer updated the Hyperperameters:  [0.27357523 1.37891145 1.09493401]
The Autonomus Experimente

differential_evolution step 6: f(x)= -0.477784
differential_evolution step 7: f(x)= -0.477784
The acquisition function optimization resulted in: 
     x:  [[1.63818973 8.95229047]]
  f(x):  [-0.47778427]
acquisition funciton optimization tolerance changed to:  0.04777842680175459
Next points to be requested: 
[[1.63818973 8.95229047]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.27357523 1.37891145 1.09493401]
The GPOptimizer updated the Hyperperameters:  [0.27357523 1.37891145 1.09493401]
The Autonomus Experimente

differential_evolution step 3: f(x)= -0.45503
differential_evolution step 4: f(x)= -0.45503
The acquisition function optimization resulted in: 
     x:  [[3.72097577 8.77633422]]
  f(x):  [-0.45502983]
acquisition funciton optimization tolerance changed to:  0.04550298252835226
Next points to be requested: 
[[3.72097577 8.77633422]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.27357523 1.37891145 1.09493401]
The GPOptimizer updated the Hyperperameters:  [0.27357523 1.37891145 1.09493401]
The Autonomus Experimenter 

...

differential_evolution step 1: f(x)= -0.429611
differential_evolution step 2: f(x)= -0.440628
differential_evolution step 3: f(x)= -0.440628
differential_evolution step 4: f(x)= -0.44128
differential_evolution step 5: f(x)= -0.44128
differential_evolution step 6: f(x)= -0.44128
differential_evolution step 7: f(x)= -0.446612
The acquisition function optimization resulted in: 
     x:  [[4.66942691 0.24639084]]
  f(x):  [-0.44661246]
acquisition funciton optimization tolerance changed to:  0.0446612460737503
Next points to be requested: 
[[4.66942691 0.24639084]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameter

differential_evolution step 4: f(x)= -0.429873
differential_evolution step 5: f(x)= -0.429873
differential_evolution step 6: f(x)= -0.430525
differential_evolution step 7: f(x)= -0.430819
The acquisition function optimization resulted in: 
     x:  [[7.23189196 1.34213717]]
  f(x):  [-0.4308195]
acquisition funciton optimization tolerance changed to:  0.04308194994352448
Next points to be requested: 
[[7.23189196 1.34213717]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.27357523 1.37891145 1.09493401]
The GPOptimiz

differential_evolution step 5: f(x)= -0.425015
differential_evolution step 6: f(x)= -0.425015
The acquisition function optimization resulted in: 
     x:  [[2.71296619 8.29793241]]
  f(x):  [-0.42501521]
acquisition funciton optimization tolerance changed to:  0.042501520865599066
Next points to be requested: 
[[2.71296619 8.29793241]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.27357523 1.37891145 1.09493401]
The GPOptimizer updated the Hyperperameters:  [0.27357523 1.37891145 1.09493401]
The Autonomus Experiment

differential_evolution step 13: f(x)= -0.424774
differential_evolution step 14: f(x)= -0.424774
differential_evolution step 15: f(x)= -0.424774
differential_evolution step 16: f(x)= -0.424774
differential_evolution step 17: f(x)= -0.42545
differential_evolution step 18: f(x)= -0.427266
The acquisition function optimization resulted in: 
     x:  [[9.98170867 6.52511944]]
  f(x):  [-0.427266]
acquisition funciton optimization tolerance changed to:  0.042726600124923214
Next points to be requested: 
[[9.98170867 6.52511944]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparame

fvGP successfully killed the training.
The autonomous experiment was concluded successfully
length of the dataset is now:  100







## Now let's plot the posterior mean after the experiment has concluded

In [9]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x,my_ae.y]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [10]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [11]:
from gpcam.autonomous_experimenter import AutonomousExperimenterFvGP


def instrument(data):
    for entry in data:
        entry["values"] = griddata(x,y,entry["position"],method = "nearest", fill_value = 0)[0]
        entry["value positions"] = np.array([[0],[1]])
    return data

input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((22,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1,instrument,np.ones((22)),hps_bounds,
                                     init_dataset_size= 10)
my_fvae.train()
my_fvae.go(N = 100)

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
CAUTION: fvGP reports that you h

differential_evolution step 1: f(x)= -16.2693
The acquisition function optimization resulted in: 
     x:  [[ -0.65829773  -0.86533584   0.33019482   2.11371593   0.56276251
   -0.39762901   0.16872981   1.35428414   0.31344255   1.08029161
    1.53244688  -2.10354421   0.43329758  -3.00569595  45.18794663
  -21.91467077  25.23428246 -18.87934516  35.67350787  17.11304266
  -27.47662718]]
  f(x):  [-16.26934038]
acquisition funciton optimization tolerance changed to:  1.6269340382180149
Next points to be requested: 
[[ -0.65829773  -0.86533584   0.33019482   2.11371593   0.56276251
   -0.39762901   0.16872981   1.35428414   0.31344255   1.08029161
    1.53244688  -2.10354421   0.43329758  -3.00569595  45.18794663
  -21.91467077  25.23428246 -18.87934516  35.67350787  17.11304266
  -27.47662718]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++

differential_evolution step 1: f(x)= -15.9202
The acquisition function optimization resulted in: 
     x:  [[ -0.2835205   -0.19705381  -0.2318407    0.89054458   0.58670553
   -0.05838955   0.3239784    2.87070042   1.93922685   1.76020631
    0.17425979  -0.85627279   1.52945268   1.78877232 -39.26785743
    0.48982235  25.14024781 -35.71428464 -30.42267777 -16.20912415
  -11.87288161]]
  f(x):  [-15.92017333]
acquisition funciton optimization tolerance changed to:  1.592017332601296
Next points to be requested: 
[[ -0.2835205   -0.19705381  -0.2318407    0.89054458   0.58670553
   -0.05838955   0.3239784    2.87070042   1.93922685   1.76020631
    0.17425979  -0.85627279   1.52945268   1.78877232 -39.26785743
    0.48982235  25.14024781 -35.71428464 -30.42267777 -16.20912415
  -11.87288161]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++

differential_evolution step 1: f(x)= -15.4134
The acquisition function optimization resulted in: 
     x:  [[-2.41237416e-01 -3.28011318e-01 -3.82177551e-02  1.03061886e+00
  -7.95847768e-02 -2.94915523e-01  1.94829943e-01 -1.11085806e+00
   2.30618406e-01 -1.56580504e+00 -3.59786381e+00 -3.59954979e-01
  -5.11352521e-01 -3.76295157e-01  1.89630438e+01  1.41021655e+01
   2.55318224e+01  6.68553330e+01  9.42470406e+00  5.23083554e+00
  -2.73098516e+01]]
  f(x):  [-15.41339881]
acquisition funciton optimization tolerance changed to:  1.5413398805055856
Next points to be requested: 
[[-2.41237416e-01 -3.28011318e-01 -3.82177551e-02  1.03061886e+00
  -7.95847768e-02 -2.94915523e-01  1.94829943e-01 -1.11085806e+00
   2.30618406e-01 -1.56580504e+00 -3.59786381e+00 -3.59954979e-01
  -5.11352521e-01 -3.76295157e-01  1.89630438e+01  1.41021655e+01
   2.55318224e+01  6.68553330e+01  9.42470406e+00  5.23083554e+00
  -2.73098516e+01]]
Sending request to instrument ...
Data received
Checking if dat

differential_evolution step 1: f(x)= -15.1111
The acquisition function optimization resulted in: 
     x:  [[ -0.6618553   -0.77808345   0.32431468   1.12052549   0.92834199
   -0.48505671  -0.29405439   0.62215686   0.36126379  -2.58477149
   -1.90994824  -1.1033898    1.23142754  -1.91052261 -45.41171713
   15.90652759  24.32884587  57.2398099  -31.32798111  16.02992561
  -36.29499597]]
  f(x):  [-15.11105815]
acquisition funciton optimization tolerance changed to:  1.5111058153186046
Next points to be requested: 
[[ -0.6618553   -0.77808345   0.32431468   1.12052549   0.92834199
   -0.48505671  -0.29405439   0.62215686   0.36126379  -2.58477149
   -1.90994824  -1.1033898    1.23142754  -1.91052261 -45.41171713
   15.90652759  24.32884587  57.2398099  -31.32798111  16.02992561
  -36.29499597]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++

...

differential_evolution step 1: f(x)= -13.4816
The acquisition function optimization resulted in: 
     x:  [[ -0.55772772  -0.30851243  -0.21656786   1.46441174   0.18394539
    0.09610593   0.21550171  -0.21288963   0.44298134   2.49417502
    2.56125006   1.89532933   1.03202419  -2.80620406  43.348569
   17.4076971  -17.03464178  56.81907126 -15.61433023  17.38885916
   24.74162165]]
  f(x):  [-13.48157521]
acquisition funciton optimization tolerance changed to:  1.3481575211338295
Next points to be requested: 
[[ -0.55772772  -0.30851243  -0.21656786   1.46441174   0.18394539
    0.09610593   0.21550171  -0.21288963   0.44298134   2.49417502
    2.56125006   1.89532933   1.03202419  -2.80620406  43.348569
   17.4076971  -17.03464178  56.81907126 -15.61433023  17.38885916
   24.74162165]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++++++

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [287.184484    16.69122048  56.19756643  23.17464046  26.83350373
  45.05562567  49.65672616  43.61987335  86.49464838  61.32476985
  50.14811891  89.27348356  89.39273633  52.4852122   62.53701226
  93.01361751  93.58503232  19.30105258  87.65235583  25.06218972
  82.52056334  90.85025539]



iteration:  90
Run Time:  27.99221968650818      seconds
Number of measurements:  90
hps:  [287.184484    16.69122048  56.19756643  23.17464046  26.83350373
  45.05562567  49.65672616  43.61987335  86.49464838  61.32476985
  50.14811891  89.27348356  89.39273633  52.4852122

differential_evolution step 1: f(x)= -13.3794
The acquisition function optimization resulted in: 
     x:  [[  0.44912002  -0.22313193  -0.39528651   1.1364122    0.63674745
   -0.30198536  -0.23081609   2.50101317  -0.86591676  -2.5975647
    2.18656033  -2.48302008   1.59506026   1.64447592  19.43728216
   18.86523643 -23.12080573 -31.69422034  30.03171388  17.8256354
   24.24222661]]
  f(x):  [-13.37940154]
acquisition funciton optimization tolerance changed to:  1.3379401536031956
Next points to be requested: 
[[  0.44912002  -0.22313193  -0.39528651   1.1364122    0.63674745
   -0.30198536  -0.23081609   2.50101317  -0.86591676  -2.5975647
    2.18656033  -2.48302008   1.59506026   1.64447592  19.43728216
   18.86523643 -23.12080573 -31.69422034  30.03171388  17.8256354
   24.24222661]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++++++

The acquisition function optimization resulted in: 
     x:  [[-7.32326941e-01 -4.20437056e-01  2.08716378e-02  1.17034013e+00
  -4.24705642e-02  2.77662860e-01  3.69720869e-01  1.98801541e+00
   6.34456707e-01 -5.57612381e-01  8.82559750e-01 -4.85445797e-01
   1.90815710e+00  3.74167104e-01 -1.11826854e+01 -1.70988521e+01
   5.37818497e+00 -2.70070418e+01  3.27365230e+01  1.14481126e+00
   3.03259311e+01]]
  f(x):  [-12.50033633]
acquisition funciton optimization tolerance changed to:  1.2500336331376531
Next points to be requested: 
[[-7.32326941e-01 -4.20437056e-01  2.08716378e-02  1.17034013e+00
  -4.24705642e-02  2.77662860e-01  3.69720869e-01  1.98801541e+00
   6.34456707e-01 -5.57612381e-01  8.82559750e-01 -4.85445797e-01
   1.90815710e+00  3.74167104e-01 -1.11826854e+01 -1.70988521e+01
   5.37818497e+00 -2.70070418e+01  3.27365230e+01  1.14481126e+00
   3.03259311e+01]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to 

population size:  20
maximum number of iterations:  20
bounds: 
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
cost function parameters:  {}
differential_evolution step 1: f(x)= -13.1396
The acquisition function optimization resulted in: 
     x:  [[ -0.25797143  -0.92418996   0.27381923   1.57307894   0.43259887
    0.32343341   0.34118095  -1.86144143   0.09752438  -1.18568204
    2.05937984  -1.85918971   0.60090613  -2.37483354 -32.41942347
   22.20005158 -20.64042863  67.05525743  32.54583874 -18.65806692
  -31

## Plotting the 0th task in a 2d slice

In [12]:
x_pred = np.zeros((10000,21))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((21))
        x_pred[counter,[0,1]] = np.array([x[i,j],y[i,j]])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)

## Back to a single task: using the GPOptimizer class directly gives you some more flexibility
We will show more soon!

In [13]:
#/usr/bin/env python
import numpy as np
from gpcam.gp_optimizer import GPOptimizer

#initialize some data
x_data = np.random.uniform(size = (100,1))
y_data = np.sin(x_data)[:,0]


#initialize the GPOptimizer
my_gpo = GPOptimizer(1,np.array([[0,1]]))
#tell() it some data
my_gpo.tell(x_data,y_data)
#initialize a GP ...
my_gpo.init_gp(np.ones(2))
#and train it
my_gpo.train_gp(np.array([[0.001,100],[0.001,100]]))

#let's make a prediction
print(my_gpo.posterior_mean(np.array([0.44])))

#now we can ask for a new point
r = my_gpo.ask()
print(r)
#putting the ask() in a loop and updating the data will
#give you all you need for your autonomous experiment

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
fvGP training started with  100  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1.]  with old log likelihood:  -95.81198588046801
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  120
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= -158.144
differential_evolution step 2: f(x)= -158.144
differential_evolution step 3: f(x)= -158.629
differential_evolution step 4: f(x)= -158.694
differential_evolution step 5: f(x)= -159.312
differential_evolution step 6: f(x)= -159.411
differential_evolution step 7: f(x)= -159.758
differential_evolution step 8: f(x)= -159.758
differential_evolution step 9: f(x)= -159.973
differential_evolution step 10: f(x)= 